In [169]:
import pandas as pd
import numpy as np
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, HoverTool, Tabs, TabPanel, Legend,  Toggle, LegendItem, CustomJS, Select, Button
from bokeh.palettes import Category20
from bokeh.layouts import column
import os

# LinkedIn Industry Performance Analysis: Algeria 2017-2025

This notebook analyses LinkedIn Hiring Rate, Skills and Skills Penetration by Gender in Algeria. 

## LinkedIn Hiring Rate

In [170]:
COUNTRY = 'Algeria'
os.environ['COUNTRY'] = COUNTRY

In [171]:
def clean_linkedin_data(excel_file):
    """Clean and prepare LinkedIn data from Excel file."""
    try:
        # Load the specific sheet with correct header row
        data_corrected = pd.read_excel(excel_file, sheet_name="2B - LHR by Ctry, Ind", header=3)
        
        # Rename columns and clean data
        data_cleaned = data_corrected.rename(columns={
            'Unnamed: 1': 'Month',
            'Unnamed: 2': 'Country',
            'Unnamed: 3': 'Industry',
            'Unnamed: 4': 'LHR (YOY)'
        })
        
        # Remove rows with missing data
        data_cleaned = data_cleaned.dropna(subset=['Month', 'Country', 'Industry', 'LHR (YOY)'])
        
        # Remove the first row (duplicate headers)
        data_cleaned = data_cleaned.iloc[1:]
        
        # Remove the column containing only NaN values
        data_cleaned = data_cleaned.drop(columns=['Unnamed: 0'])
        
        return data_cleaned
        
    except Exception as e:
        print(f"Error during data cleaning: {str(e)}")
        return None

In [172]:
def create_industry_performance_plots(excel_file):
    """Create interactive plots showing industry performance in Algeria, with toggle to filter from 2022."""
    output_notebook()

    try:
        # Clean the data
        df = clean_linkedin_data(excel_file)
        if df is None:
            print("Data cleaning failed. Please check your Excel file.")
            return

        # Filter data for Algeria
        country = os.getenv('COUNTRY')
        bd_data = df[df['Country'] == country].copy()

        # Convert Month to datetime
        bd_data['Month'] = pd.to_datetime(bd_data['Month'])

        # Calculate average LHR for each industry
        industry_avg = bd_data.groupby('Industry')['LHR (YOY)'].mean().sort_values(ascending=False)

        # Split industries into quartiles (5 industries each)
        top_5 = industry_avg.head(5).index.tolist()
        upper_mid_5 = industry_avg.iloc[5:10].index.tolist()
        lower_mid_5 = industry_avg.iloc[10:15].index.tolist()
        bottom_5 = industry_avg.iloc[15:].index.tolist()

        # Define quartile categories
        categories = [
            ('Leading Industries', top_5, 'Top Performing Industries (1st Quartile)'),
            ('Growing Industries', upper_mid_5, 'Strong Performing Industries (2nd Quartile)'),
            ('Transitioning Industries', lower_mid_5, 'Moderate Performing Industries (3rd Quartile)'),
            ('Emerging Industries', bottom_5, 'Developing Industries (4th Quartile)')
        ]

        tabs = []

        # Create one tab per industry category
        for tab_title, industries, plot_title in categories:
            # Prepare full and filtered data
            plot_data_full = bd_data[bd_data['Industry'].isin(industries)].copy()
            plot_data_filtered = plot_data_full[plot_data_full['Month'] >= '2022-01-01'].copy()

            # Create figure
            p = figure(
                title=f"LinkedIn Hiring Rate: {plot_title} in Algeria",
                x_axis_type='datetime',
                width=800,
                height=500,
                background_fill_color="#f8f9fa"
            )

            legend_items = []
            js_sources = []

            for i, industry in enumerate(industries):
                color = Category20[10][i]

                full_industry_data = plot_data_full[plot_data_full['Industry'] == industry]
                filtered_industry_data = plot_data_filtered[plot_data_filtered['Industry'] == industry]

                source = ColumnDataSource(full_industry_data)
                source_full = ColumnDataSource(full_industry_data)
                source_filtered = ColumnDataSource(filtered_industry_data)

                line = p.line(
                    x='Month',
                    y='LHR (YOY)',
                    source=source,
                    line_width=3,
                    color=color
                )

                legend_items.append((f"{industry} (Avg: {industry_avg[industry]:.2f}%)", [line]))
                js_sources.append({'source': source, 'full': source_full, 'filtered': source_filtered})

            # Add hover
            p.add_tools(HoverTool(
                tooltips=[
                    ("Month", "@Month{%b %Y}"),
                    ("LHR (YOY)", "@{LHR (YOY)}{0.00}%"),
                    ("Industry", "@Industry")
                ],
                formatters={"@Month": "datetime"},
                mode='vline'
            ))

            # Axes labels and styling
            p.xaxis.axis_label = 'Month'
            p.yaxis.axis_label = 'LinkedIn Hiring Rate (YOY %)'
            p.xaxis.axis_label_text_font_size = '12pt'
            p.yaxis.axis_label_text_font_size = '12pt'
            p.xaxis.major_label_text_font_size = '10pt'
            p.yaxis.major_label_text_font_size = '10pt'
            p.title.text_font_size = '14pt'
            p.grid.grid_line_color = "gray"
            p.grid.grid_line_alpha = 0.3

            # Add legend
            legend = Legend(
                items=legend_items,
                orientation='horizontal',
                spacing=20,
                padding=10,
                click_policy="hide",
                label_text_font_size='9pt',
                border_line_color="gray",
                border_line_alpha=0.5,
                background_fill_alpha=0.7,
                nrows=3
            )
            p.add_layout(legend, 'below')

            # Toggle button
            toggle = Toggle(label="Filter from 2022", button_type="success", active=False)

            # JS callback
            callback_code = """
                for (let i = 0; i < sources.length; i++) {
                    sources[i].data = toggle.active ? filtered[i].data : full[i].data;
                    sources[i].change.emit();
                }
                toggle.label = toggle.active ? 'Show full range' : 'Filter from 2022';
                toggle.button_type = toggle.active ? 'warning' : 'success';
        """

            callback = CustomJS(args={
                "toggle": toggle,
                "sources": [src['source'] for src in js_sources],
                "full": [src['full'] for src in js_sources],
                "filtered": [src['filtered'] for src in js_sources]
                }, code=callback_code)

            toggle.js_on_change("active", callback)

            # Combine toggle and plot
            tab_layout = column(toggle, p)
            tab = TabPanel(child=tab_layout, title=tab_title)
            tabs.append(tab)

        # Show tabs
        if tabs:
            tabs_layout = Tabs(tabs=tabs)
            show(tabs_layout)
        else:
            print("No data available for visualization.")

    except Exception as e:
        print(f"An error occurred: {str(e)}")
        print("Please check your Excel file structure and column names.")



In [173]:
def export_industry_metrics(excel_file, output_path='industry_performance_metrics.csv'):
    """Export industry performance metrics to CSV file."""
    try:
        # Clean the data
        df = clean_linkedin_data(excel_file)
        
        if df is None:
            return None
            
        # Filter data for Algeria
        bd_data = df[df['Country'] == 'Algeria'].copy()
        bd_data['Month'] = pd.to_datetime(bd_data['Month'])
        
        # Calculate metrics for each industry
        metrics_list = []
        for industry in bd_data['Industry'].unique():
            industry_data = bd_data[bd_data['Industry'] == industry]
            
            # Calculate various metrics
            metrics = {
                'Industry': industry,
                'Average_LHR': industry_data['LHR (YOY)'].mean(),
                'Max_LHR': industry_data['LHR (YOY)'].max(),
                'Min_LHR': industry_data['LHR (YOY)'].min(),
                'Volatility': industry_data['LHR (YOY)'].std(),
                'Latest_LHR': industry_data.loc[industry_data['Month'].idxmax(), 'LHR (YOY)'],
                'Growth_Trend': industry_data['LHR (YOY)'].iloc[-1] - industry_data['LHR (YOY)'].iloc[0],
                'Start_Date': industry_data['Month'].min().strftime('%Y-%m'),
                'End_Date': industry_data['Month'].max().strftime('%Y-%m')
            }
            metrics_list.append(metrics)
        
        # Create DataFrame and sort by Average LHR
        metrics_df = pd.DataFrame(metrics_list)
        metrics_df = metrics_df.sort_values('Average_LHR', ascending=False)
        
        # Add category labels
        n_industries = len(metrics_df)
        categories = ['Leading Industries'] * 5 + \
                    ['Growing Industries'] * 5 + \
                    ['Transitioning Industries'] * 5 + \
                    ['Emerging Industries'] * 5
        metrics_df['Category'] = categories[:n_industries]
        
        # Reorder columns to put Category first
        cols = ['Category'] + [col for col in metrics_df.columns if col != 'Category']
        metrics_df = metrics_df[cols]
        
        # Export to CSV
        metrics_df.to_csv(output_path, index=False)
        print(f"Metrics exported to {output_path}")
        
        return metrics_df
        
    except Exception as e:
        print(f"Error exporting metrics: {str(e)}")
        return None

# Example usage:
file_path = '../../data/LinkedIn/LinkedIn_LHR by Industry_Feb2025.xlsx'
metrics_df = export_industry_metrics(file_path, '../../data/LinkedIn/processed/Algeria_industry_metrics.csv')

Metrics exported to ../../data/LinkedIn/processed/Algeria_industry_metrics.csv


In [174]:
file_path = '../../data/LinkedIn/LinkedIn_LHR by Industry_Feb2025.xlsx'
create_industry_performance_plots(file_path)

Loading BokehJS ...

In [175]:
df = clean_linkedin_data(file_path)

In [176]:
from tabulate import tabulate
industry_grouping = metrics_df.groupby(['Category'])[['Average_LHR', 'Max_LHR','Min_LHR', 'Volatility', 'Growth_Trend']].mean().reset_index()
headers = ['Average LHR', 'Max LHR', 'Min LHR', 'Volatility (STD)', 'Growth Trend (2017-2025)']
print(tabulate(industry_grouping, headers=headers,tablefmt='fancy_grid'))

╒════╤══════════════════════════╤═══════════════╤═══════════╤═══════════╤════════════════════╤════════════════════════════╕
│    │                          │   Average LHR │   Max LHR │   Min LHR │   Volatility (STD) │   Growth Trend (2017-2025) │
╞════╪══════════════════════════╪═══════════════╪═══════════╪═══════════╪════════════════════╪════════════════════════════╡
│  0 │ Emerging Industries      │     -0.204222 │   0.61155 │  -0.504   │           0.252748 │                  -0.036875 │
├────┼──────────────────────────┼───────────────┼───────────┼───────────┼────────────────────┼────────────────────────────┤
│  1 │ Growing Industries       │      0.229189 │   4.93574 │  -0.80098 │           0.849302 │                  -0.30158  │
├────┼──────────────────────────┼───────────────┼───────────┼───────────┼────────────────────┼────────────────────────────┤
│  2 │ Leading Industries       │      0.460806 │   9.21272 │  -0.57202 │           1.24449  │                  -0.14782  │
├────┼──

# 🇩🇿 **Insights: Algeria**

The LinkedIn dataset for Algeria covers 20 industries, grouped into four quartiles according to their **average year-on-year hiring rate (LHR)** between 2017 and 2025. The quartiles reflect different growth and volatility patterns in the Algerian labor market.

---

### **Quartile #1: Leading Industries (avg LHR: 0.29–0.77%)**

* **Real Estate and Equipment Rental Services** leads with an average LHR of **0.77%**, the highest among all industries. It shows **moderate volatility (0.42%)**, suggesting relatively stable yet sustained growth across the period. (Note: this industry only has two data points)
* **Accommodation and Food Services** exhibits **high volatility (2.13%)**, with LHRs ranging from **-0.93% to 17.79%**, reflecting year-to-year spikes related to reopening after COVID-19 (5/1/21). Despite this volatility, its **growth trend remains positive (+0.21%)**.
* **Retail** and **Consumer Services** show weaker performance, both experiencing **negative growth trends (-1.38% and -0.17%)** and ending February 2025 with negative hiring rates.
* **Education**, while having the lowest average LHR in this group (**0.29%**), maintains **near-zero volatility (0.86%)** and a **stable growth trend (+0.004%)**.

> In short, Algeria’s “leading” sectors are dynamic but volatile. The hospitality and retail segments have seen sharp cycles, while education and real estate provide steadier employment momentum.

---

### **Quartile #2: Growing Industries (avg LHR: 0.20–0.26%)**

* **Hospitals and Health Care** tops this group with an average LHR of **0.26%**, though its **growth trend is negative (-0.85%)**, implying contraction after a strong 2021–22 period.
* **Transportation, Logistics, Supply Chain and Storage** maintains a **steady LHR (0.22%)** and **moderate volatility (0.72%)**, though it too shows **slight negative growth (-0.20%)**.
* **Government Administration** stands out with a **positive growth trend (+0.75%)**, indicating gradual hiring increases over time.
* **Financial Services** and **Entertainment Providers** both show **high volatility (~1%)** and **declining trends**, suggesting cyclical activity but limited sustained expansion.

---

### **Quartile #3: Transitioning Industries (avg LHR: 0.10–0.16%)**

* **Wholesale** and **Construction** have average LHRs of **0.16%** and **0.12%**, with moderate volatility (~0.65–0.69%). Construction shows **a mild positive trend (+0.12%)**, suggesting a potential rebound in hiring activity, while wholesale shows  a **negative growth trend (-0.39%)**.
* **Technology, Information, and Media** has an average LHR of **0.13%**, moderate volatility (**0.41%**), and a **neutral growth trend (+0.02%)**, indicating steady but limited digital hiring.
* **Professional Services** shows the **lowest volatility (0.37%)** in this group, suggesting relative stability despite a **negative growth trend (-0.39%)**.
* **Manufacturing** records **slightly higher volatility (0.61%)** and **negative growth (-0.18%)**, reflecting slower recovery in traditional production sectors.

> These “transitioning” industries display mixed trajectories: **construction** and **technology** are stabilizing, while **wholesale**, **manufacturing** and **professional services** are showing signs of contraction.

---

### **Quartile #4: Emerging Industries (avg LHR: -0.53–0.10%)**

* **Oil, Gas, and Mining**, traditionally Algeria’s key export sector, has an **average LHR of 0.10%** but a **negative growth trend (-0.44%)**, reflecting cyclical activity with limited net job creation.
* **Utilities** shows an **average LHR of -0.16%** and the second **lowest volatility (0.13%)**. (Note: this industry only has two data points)
* **Administrative and Support Services** reports a **negative average LHR (-0.22%)** but a **strong positive growth trend (+0.43%)**, suggesting a recent uptick in hiring momentum. (Note: this industry only has two data points)
* **Farming, Ranching, and Forestry** has the **lowest average LHR (-0.53%)** but a **slight positive growth (+0.06%)**. (Note: this industry only has two data points)

---

### **Overall Observations**

* Across all industries, **volatility is present**, with multiple sectors showing large hiring swings (some exceeding ±10%).
* Overall **growth trends are mostly negative**, meaning that current momentum is driven by past peaks rather than sustained expansion.
* **Government Administration** and **Real Estate and Equipment Rental Services** are the only sectors with clear positive growth trends and positive latest LHR.

## Skills Distribution Analysis in Algeria's Labor Market

This analysis shows the top skills in each industries from LinkedIn skills assumed and mentioned by its users. 

In [177]:
def create_industry_performance_dict(excel_file):
    """Create a dictionary with industry performance metrics split into 4 quartiles."""
    try:
        # Clean data
        df = clean_linkedin_data(excel_file)
        
        if df is None:
            return None
            
        # Filter data for Algeria and convert Month to datetime
        bd_data = df[df['Country'] == 'Algeria'].copy()
        bd_data['Month'] = pd.to_datetime(bd_data['Month'])
        
        # Initialize performance dictionary with 4 quartiles
        performance_dict = {
            'leading_industries': {},      # Top 5 (1st quartile)
            'growing_industries': {},      # Next 5 (2nd quartile)
            'transitioning_industries': {}, # Next 5 (3rd quartile)
            'emerging_industries': {}      # Last 5 (4th quartile)
        }
        
        # Calculate metrics for each industry
        industry_metrics = {}
        for industry in bd_data['Industry'].unique():
            industry_data = bd_data[bd_data['Industry'] == industry]
            
            # Calculate industry metrics
            metrics = {
                'avg_lhr': industry_data['LHR (YOY)'].mean(),
                'max_lhr': industry_data['LHR (YOY)'].max(),
                'min_lhr': industry_data['LHR (YOY)'].min(),
                'latest_lhr': industry_data.loc[industry_data['Month'].idxmax(), 'LHR (YOY)'],
                'start_date': industry_data['Month'].min().strftime('%Y-%m'),
                'end_date': industry_data['Month'].max().strftime('%Y-%m'),
                'trend': industry_data['LHR (YOY)'].iloc[-1] - industry_data['LHR (YOY)'].iloc[0],
                'volatility': industry_data['LHR (YOY)'].std()
            }
            industry_metrics[industry] = metrics
        
        # Sort industries by average LHR
        sorted_industries = sorted(industry_metrics.items(), 
                                 key=lambda x: x[1]['avg_lhr'], 
                                 reverse=True)
        
        # Split into 4 groups of 5 industries each
        total_industries = len(sorted_industries)
        
        # Populate performance dictionary
        for i, (industry, metrics) in enumerate(sorted_industries):
            if i < 5:  # First 5 industries
                performance_dict['leading_industries'][industry] = metrics
            elif i < 10:  # Next 5 industries
                performance_dict['growing_industries'][industry] = metrics
            elif i < 15:  # Next 5 industries
                performance_dict['transitioning_industries'][industry] = metrics
            else:  # Last 5 industries
                performance_dict['emerging_industries'][industry] = metrics
        
        return performance_dict
            
    except Exception as e:
        print(f"An error occurred: {str(e)}")
        return None

# Example usage:
file_path = '../../data/LinkedIn/LinkedIn_LHR by Industry_Feb2025.xlsx'
indust_dict = create_industry_performance_dict(file_path)

In [178]:
# Ruta del archivo Excel
file_path = '../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx'

# # Verificar las hojas del archivo
excel_file = pd.ExcelFile(file_path)
print(excel_file.sheet_names)

# Cargar la hoja específica "2A - SGP Ctry Ind"
sheet_name = "2A - SGP Ctry Ind"
data = pd.read_excel(file_path, sheet_name=sheet_name)

# Cargar nuevamente con encabezado correcto (fila 4, index 3)
data_corrected = pd.read_excel(file_path, sheet_name=sheet_name, header=3)

#Renombrar columnas y limpiar datos
data_cleaned = data_corrected.rename(columns={
    'Unnamed: 2': 'Country',
    'Unnamed: 3': 'Industry',
    'Unnamed: 4': 'Skill',
    'Unnamed: 5': 'Skill Rank'
})

#Eliminar filas que no contengan datos válidos
data_cleaned = data_cleaned.dropna(subset=['Country', 'Industry', 'Skill', 'Skill Rank'])

# Eliminar la primera línea (que contiene encabezados duplicados)
data_cleaned = data_cleaned.iloc[4:]
print(data_cleaned.columns)

# Eliminar la columna que contiene únicamente valores NaN
data_cleaned = data_cleaned.drop(columns=['Unnamed: 0', 'Unnamed: 1'])

['COVER', '1 - Read_me', '2A - SGP Ctry Ind', '2B - SGF Ctry Ind Yr', '3A - SPP Ctry', '3B - SPP Ctry Ind', '3B - SPP Ctry Ind Gen', 'Ref - Industries', 'Ref - Country List']
Index(['Unnamed: 0', 'Unnamed: 1', 'Country', 'Industry', 'Skill',
       'Skill Rank'],
      dtype='object')


In [179]:
import pandas as pd
import numpy as np
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, HoverTool, Tabs, TabPanel, Range1d
from bokeh.palettes import Spectral6
from bokeh.layouts import column
from bokeh.transform import factor_cmap
from bokeh.io import output_notebook

def clean_skills_data(skills_file):
    """Clean and prepare skills genome data."""
    try:
        # Load and clean skills data
        data_corrected = pd.read_excel(skills_file, sheet_name="2A - SGP Ctry Ind", header=3)
        
        data_cleaned = data_corrected.rename(columns={
            'Unnamed: 2': 'Country',
            'Unnamed: 3': 'Industry',
            'Unnamed: 4': 'Skill',
            'Unnamed: 5': 'Skill Rank'
        })
        
        data_cleaned = data_cleaned.dropna(subset=['Country', 'Industry', 'Skill', 'Skill Rank'])
        data_cleaned = data_cleaned.iloc[4:]
        data_cleaned = data_cleaned.drop(columns=['Unnamed: 0', 'Unnamed: 1'])
        
        # Convert Skill Rank to numeric
        data_cleaned['Skill Rank'] = pd.to_numeric(data_cleaned['Skill Rank'], errors='coerce')
        data_cleaned = data_cleaned.dropna(subset=['Skill Rank'])
        
        return data_cleaned
    except Exception as e:
        print(f"Error during skills data cleaning: {str(e)}")
        return None

In [180]:
def export_skills_metrics(skills_file, lhr_file, output_path='industry_skills_metrics.csv'):
    """Export skills rankings and metrics for each industry category."""
    try:
        # Get industry categories from LHR data
        industry_dict = create_industry_performance_dict(lhr_file)
        
        # Clean skills data
        skills_data = clean_skills_data(skills_file)
        
        if skills_data is None or industry_dict is None:
            return None
        
        # Filter for Algeria
        country = os.environ['COUNTRY']
        bd_skills = skills_data[skills_data['Country'] == country].copy()
        
        # Prepare data for export
        export_data = []
        
        categories = [
            ('Leading Industries', industry_dict['leading_industries']),
            ('Growing Industries', industry_dict['growing_industries']),
            ('Transitioning Industries', industry_dict['transitioning_industries']),
            ('Emerging Industries', industry_dict['emerging_industries'])
        ]
        
        for category_name, industries in categories:
            for industry in industries.keys():
                industry_skills = bd_skills[bd_skills['Industry'] == industry].copy()
                
                if not industry_skills.empty:
                    # Get top 5 skills
                    top_skills = industry_skills.nsmallest(5, 'Skill Rank')
                    
                    # Add each skill to export data
                    for _, skill_row in top_skills.iterrows():
                        export_data.append({
                            'Category': category_name,
                            'Industry': industry,
                            'Skill': skill_row['Skill'],
                            'Skill_Rank': skill_row['Skill Rank']
                        })
        
        # Convert to DataFrame and export
        metrics_df = pd.DataFrame(export_data)
        metrics_df.to_csv(output_path, index=False)
        print(f"Skills metrics exported to {output_path}")
        
        return metrics_df
        
    except Exception as e:
        print(f"Error exporting skills metrics: {str(e)}")
        return None

# Example usage:
skills_file = '../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx'
lhr_file = '../../data/LinkedIn/LinkedIn_LHR by Industry_Feb2025.xlsx'
skills_metrics = export_skills_metrics(skills_file, lhr_file, '../../data/Algeria_skills_metrics.csv')

Skills metrics exported to ../../data/Algeria_skills_metrics.csv


In [181]:
skills_genome = pd.read_excel(skills_file)
skills_genome = clean_skills_data(skills_file)

skills_genome = skills_genome[skills_genome['Country']==COUNTRY]

### Transferability of Skills

In [182]:
skills_grouped = skills_genome.groupby('Skill').agg(nrIndustries=('Industry', 'size'),Industries=('Industry', list)).reset_index().sort_values('nrIndustries', ascending=False)
skills_grouped = skills_grouped[~(skills_grouped['Skill'].isin(['French', 'Arabic', 'Algeria']))]
#skills_grouped = skills_grouped[skills_grouped['nrIndustries']>1]

In [183]:
import textwrap
def wrap_and_format(cell, width=30):
    if isinstance(cell, list):
        # Join list items with newlines and wrap each item
        wrapped_items = [textwrap.fill(str(item), width=width) for item in cell]
        return '\n'.join(wrapped_items)
    else:
        # Just wrap text for non-list items
        return textwrap.fill(str(cell), width=width)

In [184]:
skills_grouped['Industries'] = skills_grouped['Industries'].apply(lambda x: wrap_and_format(x, width=40))

**Skills that most appear across industries**

In [185]:
from tabulate import tabulate
headers = ['Number of Industries', 'Industries']
skills_grouped
print(tabulate(skills_grouped.head(10).reset_index(drop=True), headers=headers,tablefmt='fancy_grid'))

╒════╤════════════════════════════════════════╤════════════════════════╤═════════════════════════════════════════╕
│    │                                        │   Number of Industries │ Industries                              │
╞════╪════════════════════════════════════════╪════════════════════════╪═════════════════════════════════════════╡
│  0 │ Search                                 │                     18 │ Accommodation and Food Services         │
│    │                                        │                        │ Administrative and Support Services     │
│    │                                        │                        │ Construction                            │
│    │                                        │                        │ Consumer Services                       │
│    │                                        │                        │ Education                               │
│    │                                        │                        │ Enterta


### **Insights**

* The most transferable skills in Algeria (excluding Arabic and French) are **Search**, **Commercial Planning**, and **Time Efficiency**. They appear across multiple sectors, showing broad relevance in service, education, and business industries.
* Following these are **Gas** and **Petroleum**, which are key technical skills linked to Algeria’s core **energy and utilities** sectors.


**Skills that least appear across industries**

In [186]:
from tabulate import tabulate
headers = ['Number of Industries', 'Industries']
skills_grouped
print(tabulate(skills_grouped.tail(20).reset_index(drop=True), headers=headers,tablefmt='fancy_grid'))

╒════╤═══════════════════════════════════╤════════════════════════╤═════════════════════════════════════════╕
│    │                                   │   Number of Industries │ Industries                              │
╞════╪═══════════════════════════════════╪════════════════════════╪═════════════════════════════════════════╡
│  0 │ Lodging                           │                      1 │ Accommodation and Food Services         │
├────┼───────────────────────────────────┼────────────────────────┼─────────────────────────────────────────┤
│  1 │ 3G Technology                     │                      1 │ Technology, Information and Media       │
├────┼───────────────────────────────────┼────────────────────────┼─────────────────────────────────────────┤
│  2 │ LTE                               │                      1 │ Technology, Information and Media       │
├────┼───────────────────────────────────┼────────────────────────┼─────────────────────────────────────────┤
│  3 │ Irr

**Insights**

- Algeria’s least transferable skills reflect specialized technical, medical, and creative expertise, which are vital within their sectors but offer limited cross-industry mobility.

In [187]:
top_half_industries = [industries for industries in indust_dict['leading_industries'].keys()] + [industries for industries in indust_dict['growing_industries']]
bottom_half_industries = [industries for industries in indust_dict['transitioning_industries'].keys()] + [industries for industries in indust_dict['emerging_industries']]

### Skills in the leading and growing industries

The skills that appear across different industries are colored differently. 

In [188]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

df = skills_genome[skills_genome['Industry'].isin(top_half_industries)][['Industry', 'Skill', 'Skill Rank']].groupby(['Industry'])['Skill'].apply(list).reset_index()
df_expanded = pd.DataFrame(df["Skill"].to_list(), index=df["Industry"]).T
# Flatten the DataFrame to find frequency of each skill
all_skills = df_expanded.values.flatten()
skills_series = (
    df_expanded
        .stack()               # long form
        .dropna()              # drop NaN/None
        .astype(str).str.strip()  # ensure strings
)

# Count skills (dict of {skill: count})
counts = skills_series.value_counts()
skill_counts = counts.to_dict()

# Define common words to be left out (these will be grey)
excluded_common_words = {"French", "Algeria", "Arabic"}  #  words to be left out

# Generate viridis color map for common skills (excluding excluded words)
common_skills = [skill for skill, count in skill_counts.items() if count > 1 and skill not in excluded_common_words]
viridis_palette = sns.color_palette("viridis", len(common_skills))
color_map = {skill: viridis_palette[i] for i, skill in enumerate(common_skills)}

# Define a neutral color for unique words
neutral_color = "lightblue"
excluded_color = "lightgrey"

# Function to apply color formatting
def highlight_common(val):
    if pd.isna(val):
        return ''
    elif skill_counts[val] > 1:
        if val in excluded_common_words:
            return f'background-color: {excluded_color}'
        return f'background-color: rgba({color_map[val][0]*255}, {color_map[val][1]*255}, {color_map[val][2]*255}, 0.8)'
    else:
        return f'background-color: {neutral_color}'


# Display the formatted DataFrame
styled_df = df_expanded.style.map(highlight_common).set_properties(**{
    'font-family': 'Open Sans',
    'font-size': '12px',  # Reduce font size for cell content
    'border-left': '1px solid black',
    'border-right': '1px solid black',
    'padding': '5px',  # Reduce padding to make the table smaller
    'width': '50px'  # Adjust column width
}).set_table_styles([
    {'selector': 'th', 'props': [('font-size', '11px')]}  # Reduce font size for column headers
])
styled_df


### Skills in the industries in the bottom half of Avg LHR

In [189]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

df = skills_genome[skills_genome['Industry'].isin(bottom_half_industries)][['Industry', 'Skill', 'Skill Rank']].groupby(['Industry'])['Skill'].apply(list).reset_index()
df_expanded = pd.DataFrame(df["Skill"].to_list(), index=df["Industry"]).T
# Flatten the DataFrame to find frequency of each skill
all_skills = df_expanded.values.flatten()
unique_skills, counts = np.unique(all_skills, return_counts=True)
skill_counts = dict(zip(unique_skills, counts))

# Define common words to be left out (these will be grey)
excluded_common_words = {"French", "Algeria", "Arabic"}  #  words to be left out

# Generate viridis color map for common skills (excluding excluded words)
common_skills = [skill for skill, count in skill_counts.items() if count > 1 and skill not in excluded_common_words]
viridis_palette = sns.color_palette("viridis", len(common_skills))
color_map = {skill: viridis_palette[i] for i, skill in enumerate(common_skills)}

# Define a neutral color for unique words
neutral_color = "lightblue"
excluded_color = "lightgrey"

# Function to apply color formatting
def highlight_common(val):
    if pd.isna(val):
        return ''
    elif skill_counts[val] > 1:
        if val in excluded_common_words:
            return f'background-color: {excluded_color}'
        return f'background-color: rgba({color_map[val][0]*255}, {color_map[val][1]*255}, {color_map[val][2]*255}, 0.8)'
    else:
        return f'background-color: {neutral_color}'


# Display the formatted DataFrame
styled_df = df_expanded.style.map(highlight_common).set_properties(**{
    'font-family': 'Open Sans',
    'font-size': '12px',  # Reduce font size for cell content
    'border-left': '1px solid black',
    'border-right': '1px solid black',
    'padding': '5px',  # Reduce padding to make the table smaller
    'width': '50px'  # Adjust column width
}).set_table_styles([
    {'selector': 'th', 'props': [('font-size', '11px')]}  # Reduce font size for column headers
])
styled_df


### Skills by Industry and Gender

In [190]:
df = pd.read_csv('../../data/LinkedIn/Skill Genome Ctry Ind Gen POOLED 2017-2023(2 - Skill Genome Ctry Ind Gen).csv', header = 5)
df = df.drop(columns=['Unnamed: 0', 'Unnamed: 1'])
df = df.dropna(subset=['Country', 'Industry', 'Gender', 'Skill', 'Skill Rank'])
df = df[df['Country']=='Algeria']
df = df.drop(columns='Country')

In [191]:
df['Skill Rank'] = df['Skill Rank'].astype(int)

In [192]:
df['Skill'] = df['Skill'].replace(r"\s+", "", regex=True)

In [193]:
df = df[~(df['Industry'].isin(['Farming, Ranching, Forestry', 'Real Estate and Equipment Rental Services', 'Utilities']))]

In [194]:
def highlight_matches(group):
    # group is a DataFrame with 2 columns: (p and q) for a given Level1 (e.g., A)
    all_vals = group.values.flatten()
    val_counts = pd.Series(all_vals).value_counts()
    matches = val_counts[val_counts > 1].index

    # Assign colors for each match
    color_map = {val: f'background-color: #{hex(hash(val) % 0xFFFFFF)[2:]:>06}' for val in matches}

    styled = pd.DataFrame('', index=group.index, columns=group.columns)

    for col in group.columns:
        styled[col] = group[col].apply(lambda x: color_map.get(x, ''))
    
    return styled

def vertical_borders(df):
    styles = pd.DataFrame("", index=df.index, columns=df.columns)
    levels = df.columns.get_level_values(0)
    for i in range(1, len(df.columns)):
        if levels[i] != levels[i - 1]:
            styles.iloc[:, i] = "border-left: 2px solid black"
    return styles


def normalize(val):
    return str(val).strip()

In [195]:
def highlight_within_industry(df: pd.DataFrame) -> pd.DataFrame:
    """
    Color a cell only if its (normalized) skill appears in BOTH genders
    within the SAME industry (any row). Colors are consistent per skill.
    """
    styles = pd.DataFrame("", index=df.index, columns=df.columns)
    lvl0 = df.columns.get_level_values(0)  # Industries
    industries = lvl0.unique()

    # normalize once for matching
    norm = df.applymap(normalize)

    for ind in industries:
        # columns for this industry (expect 2 genders)
        subcols = [c for c in df.columns if c[0] == ind]
        if len(subcols) < 2:
            continue

        sub = norm[subcols]

        # intersection of skills across all gender columns for this industry
        common = set(sub.iloc[:, 0].tolist())
        for c in sub.columns[1:]:
            common &= set(sub[c].tolist())
        common.discard("")  # ignore empty

        if not common:
            continue

        # color only cells that are in the 'common' set
        for c in subcols:
            mask = sub[c].isin(common)
            if mask.any():
                styles.loc[mask, c] = sub.loc[mask, c].map(lambda x: color_map.get(x, ""))

    return styles

def normalize(val):
    return str(val).strip()


In [196]:
import matplotlib.pyplot as plt
import numpy as np

cmap = plt.colormaps['viridis']

pivoted = (
    df.pivot(index="Skill Rank", columns=["Industry", "Gender"], values="Skill")
    .sort_index(axis=1, level=[0, 1])  # Optional: sort A→C, p→q
)

# Flatten and normalize all values
all_vals = pd.Series(pivoted.values.flatten()).dropna().astype(str).apply(normalize)
value_counts = all_vals.value_counts()
repeated_vals = value_counts[value_counts > 1].index.tolist()

# Generate color map using Viridis with alpha 0.5
cmap = plt.colormaps['tab20']
colors = cmap(np.linspace(0, 1, len(repeated_vals)))
color_map = {
    val: f'background-color: rgba({int(r*255)}, {int(g*255)}, {int(b*255)}, 0.3)'
    for val, (r, g, b, _) in zip(repeated_vals, colors)
}

# Highlight all repeated values in the DataFrame
def highlight_repeats(val):
    if pd.isna(val):
        return ''
    return color_map.get(normalize(val), '')

styled = pivoted.style.applymap(highlight_repeats)


# Optional: Tidy up the table display
styled = (
    styled
    .hide(axis="index")  # Hide index name
    .set_table_styles([
        {'selector': 'th.blank', 'props': [('display', 'none')]},
        {'selector': 'th.col_heading.level0', 'props': [('text-align', 'center')]},
        {'selector': 'th.col_heading.level1', 'props': [('text-align', 'center')]},
        {'selector': 'tbody tr:nth-child(even)', 'props': [('background-color', 'white')]}  # remove row banding
    ])
)

styled = styled.apply(vertical_borders, axis=None)

styled

/var/folders/hf/b6c3n5_56n51cn63yng8s0q80000gp/T/ipykernel_77681/3001930103.py:30: FutureWarning:

Styler.applymap has been deprecated. Use Styler.map instead.



**Insights**


* **Farming, Ranching, Forestry, Real Estate and Equipment Rental Services have no category for female skills.**
* In **Accommodation and Food Services**, **management-related skills** appear more prominently among **male profiles** than female ones.
* In **Administrative and Support Services**, male and female profiles share mostly similar skills, though **Customer Management Systems** and **Commercial Analysis** appear **only among males**.
* In **Consumer Services**, **Nonprofit work** and **Office Automation** rank higher among **female profiles**, while **Computing**—the **fourth-ranked skill for males**—does not appear among female skills.
* In **Entertainment**, **sports-related abilities** are present for **males** but absent for **females**.
* **Financial Services**; **Manufacturing**; **Professional Services**;  exhibit **similar skill distributions** across genders, indicating balanced representation.
* In **Government Administration**, there is also a similarity on skills, however, male profiles emphasize **Public Administration**, **Computing**, **Commercial Analysis**, and **Commerce**, whereas female profiles focus more on **Language Teaching** and **English Teaching**.
* In **Hospitals and Health Care**, male profiles include **Clinical Research**, **Surgery**, and **Healthcare Management**, while female profiles feature more **Patient Care** and **Drawing Blood** skills.
* In **Retail**, female profiles show stronger presence in **Couture**, **Team Spirit**, and **Fashion Design**, while male profiles highlight **Store Management**, **Retail Operations**, and **Commercial Planning**.

### Skill difference between genders

In [197]:
from tabulate import tabulate
summary = {}
for level1 in pivoted.columns.get_level_values(0).unique():
    col_p = (level1, 'female')
    col_q = (level1, 'male')

    rank_matches = sum(
        normalize(pivoted.at[rank, col_p]) == normalize(pivoted.at[rank, col_q])
        for rank in pivoted.index
    )

    # Common values regardless of rank
    values_p = pivoted[col_p].dropna().astype(str).apply(normalize).tolist()
    values_q = pivoted[col_q].dropna().astype(str).apply(normalize).tolist()
    common_values = set(values_p).intersection(values_q)

    summary[level1] = {
        'Rank+Value Matches': rank_matches,
        'Common Value Matches': len(common_values),
        'Match Rate (%)': (rank_matches / len(pivoted)) * 100
    }

# Convert to DataFrame
summary_df = pd.DataFrame.from_dict(summary, orient='index')
summary_df.index.name = 'Level1 Group'
summary_df = summary_df.sort_values(by='Match Rate (%)', ascending=False)
# Print table
from tabulate import tabulate
headers = ['Industry', 'Rank+Skill\nMatches', 'Common\nSkills', 'Skill+Rank Match (%)']
print(tabulate(summary_df.reset_index(), headers=headers, tablefmt='fancy_grid'))

╒════╤═════════════════════════════════════════════════════╤══════════════╤══════════╤════════════════════════╕
│    │ Industry                                            │   Rank+Skill │   Common │   Skill+Rank Match (%) │
│    │                                                     │      Matches │   Skills │                        │
╞════╪═════════════════════════════════════════════════════╪══════════════╪══════════╪════════════════════════╡
│  0 │ Government Administration                           │            5 │        5 │                     50 │
├────┼─────────────────────────────────────────────────────┼──────────────┼──────────┼────────────────────────┤
│  1 │ Wholesale                                           │            5 │        7 │                     50 │
├────┼─────────────────────────────────────────────────────┼──────────────┼──────────┼────────────────────────┤
│  2 │ Administrative and Support Services                 │            4 │        6 │                  

**Insights**

- Although there are a lot of industries with matching skills, the position in which they appear match the most for Government Administration; Wholesale.

## Skill Genome Pooled by Country (2017 - 2024)

In [198]:
import pandas as pd
import numpy as np

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import (
    ColumnDataSource, HoverTool, Legend, LegendItem,
    Tabs, Panel
)
from bokeh.palettes import Category10
from bokeh.transform import dodge


output_notebook()

# -----------------------------
# Helper: read & clean data
# -----------------------------
def clean_skill_data(excel_file):
    """Clean and prepare skill penetration data from Excel file."""
    # Sheet and header as in your original code
    data = pd.read_excel(excel_file, sheet_name="3A - SPP Ctry", header=5)

    required_columns = [
        'Country', 'Skill',
        'Average',
        'Global',
        'Relative'
    ]
    missing = [c for c in required_columns if c not in data.columns]
    if missing:
        print("Missing columns:", missing)
        print("Available:", data.columns.tolist())
        return None

    data = data.dropna(subset=required_columns)

    data['Country'] = data['Country'].str.strip()

    return data


# -----------------------------
# Main plotting function
# -----------------------------
def plot_relative_penetration_by_peer_groups(excel_file):
    df = clean_skill_data(excel_file)
    if df is None:
        return

    # Peer groups
    peer_groups = {
        "MENA (regional peers)": [
            "Algeria", "Egypt", "Iraq", "Jordan", "Morocco", "Tunisia"
        ],
        "Non-MENA (structural peers)": [
            "Algeria", "Uzbekistan", "Ecuador", "Peru", "Ghana", "Vietnam", "Colombia"
        ],
        "Non-MENA (aspirational peers)": [
            "Algeria", "Chile", "Kazakhstan", "Malaysia", "Poland", "Romania", "Turkey"
        ]
    }

    # Preferred skill order if available
    preferred_skill_order = [
        "Soft Skills", "Tech Skills", "Business Skills",
        "Disruptive Tech", "Green Skills"
    ]

    tabs = []

    for group_name, country_list in peer_groups.items():
        df_group = df[df['Country'].isin(country_list)].copy()
        if df_group.empty:
            print(f"No data for group: {group_name}")
            continue

        # Use only relative penetration
        grp = (
            df_group
            .groupby(['Skill', 'Country'])['Relative']
            .mean()
            .reset_index()
        )

        # Order skills
        skills_in_data = grp['Skill'].unique().tolist()
        # keep preferred order when available
        skill_order = [s for s in preferred_skill_order if s in skills_in_data]
        for s in skills_in_data:
            if s not in skill_order:
                skill_order.append(s)

        # Pivot: rows = Skill, cols = Country
        pivot = grp.pivot(index='Skill', columns='Country',
                          values='Relative') \
                    .reindex(skill_order)

        countries_in_data = [c for c in country_list if c in pivot.columns]
        if not countries_in_data:
            print(f"No matching countries with data in group: {group_name}")
            continue

        pivot = pivot[countries_in_data].reset_index()
        pivot.columns.name = None  # clean up
        source = ColumnDataSource(pivot)

        # Figure
        p = figure(
            x_range=skill_order,
            height=450,
            width=900,
            title=f"Relative Skill Group Penetration – {group_name}",
            toolbar_location="above",
            background_fill_color="#ffffff"
        )

        n_countries = len(countries_in_data)
        # total width of group; each bar = group_width / n_countries
        group_width = 0.8
        bar_width = group_width / n_countries
        start = -group_width / 2 + bar_width / 2

        colors = Category10[max(3, min(10, n_countries))]

        legend_items = []

        for i, country in enumerate(countries_in_data):
            offset = start + i * bar_width

            r = p.vbar(
                x=dodge('Skill', offset, range=p.x_range),
                top=country,
                width=bar_width * 0.9,
                source=source,
                color=colors[i % len(colors)],
                name=country
            )

            # Hover only for this renderer
            hover = HoverTool(
                renderers=[r],
                tooltips=[
                    ("Country", country),
                    ("Relative penetration", f"@{country}{{0.00}}")
                ]
            )
            p.add_tools(hover)

            legend_items.append(LegendItem(label=country, renderers=[r]))

        # Combine legend
        legend = Legend(items=legend_items)
        p.add_layout(legend, 'below')
        p.legend.orientation = "horizontal"
        p.legend.location = "center"
        p.legend.label_text_font_size = "9pt"

        p.xaxis.axis_label = "Skill group"
        p.yaxis.axis_label = "Relative skill group penetration"
        p.xaxis.major_label_orientation = 0.8
        p.y_range.start = 0

        # Remove vertical grid lines for cleaner look
        p.xgrid.grid_line_color = None

        tab = TabPanel(child=p, title=group_name)
        tabs.append(tab)

    if tabs:
        show(Tabs(tabs=tabs))
    else:
        print("No valid data to plot.")


# ---- Run it ----
excel_path = "../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx"
plot_relative_penetration_by_peer_groups(excel_path)


Loading BokehJS ...

## Skill Genome Pooled by Country and Industry (2017 - 2024)

In [199]:
import pandas as pd

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import (
    ColumnDataSource, HoverTool, Legend, LegendItem,
    CustomJS, Dropdown
)
from bokeh.layouts import column
from bokeh.palettes import Category10
from bokeh.transform import dodge

output_notebook()

# -----------------------------
# 1. Load + clean data
# -----------------------------
def clean_skill_data(excel_file):
    df = pd.read_excel(excel_file, sheet_name="3B - SPP Ctry Ind", header=5)

    required = ["Country", "Industry", "Skill", "Average", "Global", "Relative"]
    missing = [c for c in required if c not in df.columns]
    if missing:
        print("Missing:", missing)
        print("Available:", df.columns.tolist())
        return None

    df = df.dropna(subset=required)
    df["Country"] = df["Country"].str.strip()
    df["Industry"] = df["Industry"].str.strip()
    df["Skill"] = df["Skill"].str.strip()

    return df


def plot_relative_penetration_mena_only(excel_file):
    df = clean_skill_data(excel_file)
    if df is None:
        return

    # ---- MENA regional peers only ----
    mena_countries = ["Algeria", "Egypt", "Iraq", "Jordan", "Morocco", "Tunisia"]
    df_mena = df[df["Country"].isin(mena_countries)].copy()
    if df_mena.empty:
        print("No data for MENA peers.")
        return

    # Preferred skill order
    preferred_skill_order = [
        "Soft Skills", "Tech Skills", "Business Skills",
        "Disruptive Tech", "Green Skills"
    ]

    # Aggregate: mean Relative by (Industry, Skill, Country)
    g = (
        df_mena
        .groupby(["Industry", "Skill", "Country"])["Relative"]
        .mean()
        .reset_index()
    )

    # Countries actually present in data
    countries = [c for c in mena_countries if c in g["Country"].unique()]
    if not countries:
        print("No MENA countries with Relative data.")
        return

    # All industries in this subset
    industries = sorted(g["Industry"].unique().tolist())

    # -----------------------------
    # Build a dict: industry -> data dict for ColumnDataSource
    # data[industry] = {"Skill": [...], "Algeria":[...], "Egypt":[...], ...}
    # -----------------------------
    industry_data = {}

    for ind in industries:
        sub = g[g["Industry"] == ind].copy()

        # All skills in this industry
        skills_raw = sub["Skill"].unique().tolist()

        # enforce preferred skill order, then add remaining
        skill_order = [s for s in preferred_skill_order if s in skills_raw]
        for s in skills_raw:
            if s not in skill_order:
                skill_order.append(s)

        # Initialize dict for this industry
        data_dict = {"Skill": skill_order}

        for c in countries:
            vals = []
            for s in skill_order:
                match = sub[(sub["Country"] == c) & (sub["Skill"] == s)]
                if not match.empty:
                    vals.append(float(match["Relative"].iloc[0]))
                else:
                    vals.append(0.0)
            data_dict[c] = vals

        industry_data[ind] = data_dict

    # -----------------------------
    # Initial industry and source
    # -----------------------------
    initial_industry = industries[0]
    initial_data = industry_data[initial_industry]

    source = ColumnDataSource(initial_data)

    # -----------------------------
    # Figure
    # -----------------------------
    p = figure(
        x_range=initial_data["Skill"],
        height=450,
        width=900,
        title=f"Relative Skill Penetration – MENA Peers – {initial_industry}",
        toolbar_location="above",
        background_fill_color="#ffffff"
    )

    n = len(countries)
    group_width = 0.8
    bar_width = group_width / n
    start = -group_width / 2 + bar_width / 2

    colors = Category10[max(3, min(10, n))]
    legend_items = []

    for i, country in enumerate(countries):
        offset = start + i * bar_width

        r = p.vbar(
            x=dodge("Skill", offset, range=p.x_range),
            top=country,
            width=bar_width * 0.9,
            source=source,
            color=colors[i % len(colors)],
            name=country
        )

        hover = HoverTool(
            renderers=[r],
            tooltips=[
                ("Skill group", "@Skill"),
                ("Country", country),
                ("Relative penetration", f"@{country}{{0.00}}")
            ]
        )
        p.add_tools(hover)

        legend_items.append(LegendItem(label=country, renderers=[r]))

    legend = Legend(items=legend_items)
    p.add_layout(legend, "below")
    p.legend.orientation = "horizontal"
    p.legend.location = "center"
    p.legend.label_text_font_size = "9pt"

    p.xaxis.axis_label = "Skill group"
    p.yaxis.axis_label = "Relative skill group penetration"
    p.xaxis.major_label_orientation = 0.8
    p.y_range.start = 0
    p.xgrid.grid_line_color = None

    # -----------------------------
    # Dropdown to change industry
    # -----------------------------
    menu = [(ind, ind) for ind in industries]
    dropdown = Dropdown(
        label="Select industry",
        menu=menu,
        width=300
    )

    callback = CustomJS(
        args=dict(
            source=source,
            all_data=industry_data,
            plot=p
        ),
        code="""
            const selected = cb_obj.item;   // industry name from menu
            const new_data = all_data[selected];

            // Overwrite entire data of the source
            source.data = new_data;
            source.change.emit();

            // Update x-axis factors (skill groups)
            plot.x_range.factors = new_data['Skill'];

            // Update title
            plot.title.text = "Relative Skill Penetration \u2013 MENA Peers \u2013 " + selected;

            // Update dropdown label so user sees current selection
            cb_obj.label = "Select industry: " + selected;
        """
    )

    dropdown.js_on_event("menu_item_click", callback)

    # -----------------------------
    # Show
    # -----------------------------
    show(column(dropdown, p))


# ---- Run it ----
excel_path = "../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx"
plot_relative_penetration_mena_only(excel_path)





Loading BokehJS ...

In [200]:
# read data 

# skill gender, indsutry, country
file_path = "../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx"
skill_gender = pd.read_excel(file_path, sheet_name="3B - SPP Ctry Ind Gen", header=5)
# select Country, Industry, Skill, Gender, Relative Importance and Skill Group Penetration
skill_gender = skill_gender[["Country", "Industry", "Skill", "Gender", "Relative Importance", "Skill Group Penetration"]]

# skill flow by country and industry 

skill_flow = pd.read_excel(file_path, sheet_name="2B - SGF Ctry Ind Yr", header=5)
# select Country, Industry, Skill, Year, Skill, Skill Rank
skill_flow = skill_flow[["Country", "Industry", "Skill", "Year", "Skill Rank"]]

In [201]:
import pandas as pd
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, CustomJS, Dropdown, HoverTool
from bokeh.layouts import column
from bokeh.palettes import Category10

output_notebook()

# -------------------------------------------------------------------------
# README-style explanation (optional)
# -------------------------------------------------------------------------
"""
Relative Importance (Skill Genome – LinkedIn):

Relative Importance is a TF-IDF–based weight that captures how strongly a
skill characterizes a given (Country × Industry × Gender) group.
It is computed by normalizing each skill’s TF-IDF score so the weights
sum to 1. A higher value means the skill is more distinctive or central
for that gender in that industry.
"""

# -----------------------------
# Load + prepare data
# -----------------------------
file_path = "../../data/LinkedIn/Skill Genome and Skills Pen 2025.xlsx"
df = pd.read_excel(file_path, sheet_name="3B - SPP Ctry Ind Gen", header=5)

df.columns = df.columns.str.strip()

df = df[["Country", "Industry", "Skill", "Gender",
         "Relative Importance", "Skill Group Penetration"]]

# Keep only Algeria
dz = df[df["Country"] == "Algeria"].copy()

# Pivot so we have female and male columns
pivot = dz.pivot_table(
    index=["Industry", "Skill"],
    columns="Gender",
    values="Relative Importance",
    aggfunc="mean"
).reset_index()

pivot = pivot.fillna(0)

industries = pivot["Industry"].unique().tolist()

# Build a dictionary {industry: dataframe_dict}
industry_data = {}
for ind in industries:
    sub = pivot[pivot["Industry"] == ind].copy()

    # Ensure columns exist
    if "female" not in sub.columns:
        sub["female"] = 0
    if "male" not in sub.columns:
        sub["male"] = 0

    industry_data[ind] = {
        "Skill": sub["Skill"].tolist(),
        "female": sub["female"].tolist(),
        "male": sub["male"].tolist()
    }

# Initial industry to display
initial = industries[0]

source = ColumnDataSource(data=industry_data[initial])

# -----------------------------
# Create figure
# -----------------------------
p = figure(
    x_range=(0, max(source.data["female"] + source.data["male"]) * 1.2),
    y_range=source.data["Skill"],
    width=750,
    height=450,
    title=f"Gender Skill Profile – {initial}",
    toolbar_location=None
)

# Lines connecting female → male
p.segment(
    x0="female", y0="Skill",
    x1="male",   y1="Skill",
    source=source,
    line_width=2,
    color="gray"
)

# Female dots
female_dots = p.scatter(
    x="female", y="Skill",
    size=9,
    color=Category10[3][0],
    source=source,
    legend_label="Female"
)

# Male dots
male_dots = p.scatter(
    x="male", y="Skill",
    size=9,
    color=Category10[3][1],
    source=source,
    legend_label="Male"
)

# -----------------------------
# Correct Tooltips
# -----------------------------
p.add_tools(HoverTool(
    renderers=[female_dots],
    tooltips=[
        ("Skill", "@Skill"),
        ("Gender", "Female"),
        ("Relative Importance", "@female{0.000}")
    ]
))

p.add_tools(HoverTool(
    renderers=[male_dots],
    tooltips=[
        ("Skill", "@Skill"),
        ("Gender", "Male"),
        ("Relative Importance", "@male{0.000}")
    ]
))

# Cosmetics
p.legend.location = "bottom_center"
p.legend.orientation = "horizontal"
p.xaxis.axis_label = "Relative Importance (TF-IDF weighted)"
p.yaxis.axis_label = "Skill"
p.xgrid.grid_line_color = None

# -----------------------------
# JS callback for dropdown
# -----------------------------
callback = CustomJS(
    args=dict(
        source=source,
        all_data=industry_data,
        plot=p
    ),
    code="""
        const selected = cb_obj.item;
        const new_data = all_data[selected];

        source.data['Skill']  = new_data['Skill'];
        source.data['female'] = new_data['female'];
        source.data['male']   = new_data['male'];
        source.change.emit();

        plot.y_range.factors = new_data['Skill'];
        plot.title.text = "Gender Skill Profile – " + selected;
    """
)

menu = [(ind, ind) for ind in industries]
dropdown = Dropdown(label="Select Industry", menu=menu, width=250)
dropdown.js_on_event("menu_item_click", callback)

# -----------------------------
# Show layout
# -----------------------------
show(column(dropdown, p))





Loading BokehJS ...

### Skill flow

In [202]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# ---- 1. Filter to country ----
country = "Algeria"

df = skill_flow[skill_flow["Country"] == country].copy()
df = df.sort_values(["Industry", "Year", "Skill Rank"])

industries = sorted(df["Industry"].unique())

# ---- 2. Define a fixed palette of EXACTLY 10 distinct colors ----
palette10 = px.colors.qualitative.T10  # 10 very clean distinct colors

# ---- 3. Initial Industry ----
initial_industry = industries[0]

fig = go.Figure()
trace_industry = []

for ind in industries:
    df_ind = df[df["Industry"] == ind].copy()

    # take the top 10 most frequent skills in this industry
    top_k = 10
    top_skills = df_ind["Skill"].value_counts().head(top_k).index.tolist()
    df_ind = df_ind[df_ind["Skill"].isin(top_skills)].copy()

    df_ind["Skill Rank"] = df_ind["Skill Rank"].astype(int)

    # assign colors ONLY to these 10 skills
    color_map = {skill: palette10[i] for i, skill in enumerate(top_skills)}

    for skill in top_skills:
        sd = df_ind[df_ind["Skill"] == skill].sort_values("Year")
        if sd.empty:
            continue

        visible_flag = (ind == initial_industry)

        fig.add_trace(
            go.Scatter(
                x=sd["Year"],
                y=sd["Skill Rank"],
                mode="lines+markers",
                name=skill,
                legendgroup=skill,
                line=dict(color=color_map[skill], width=3, shape="spline"),
                marker=dict(size=10),
                visible=visible_flag,
                hovertemplate=(
                    f"<b>{skill}</b><br>"
                    f"Industry: {ind}<br>"
                    "Year: %{x}<br>"
                    "Rank: %{y}<extra></extra>"
                )
            )
        )

        trace_industry.append(ind)

# ---- 4. Dropdown menu ----
buttons = []
for ind in industries:
    visible = [trace_industry[i] == ind for i in range(len(trace_industry))]

    buttons.append(
        dict(
            label=ind,
            method="update",
            args=[
                {"visible": visible},
                {"title": f"{country} – Skill rank over time in {ind} (top 10 skills)"},
            ],
        )
    )

fig.update_layout(
    updatemenus=[
        dict(
            buttons=buttons,
            direction="down",
            x=0.03,
            xanchor="left",
            y=1.13,
            yanchor="top",
        )
    ]
)

# ---- 5. Axes & Style ----
fig.update_yaxes(autorange="reversed", title="Skill rank (1 = top)")
fig.update_xaxes(title="Year", tickmode="linear")

fig.update_layout(
    title=f"{country} – Skill rank over time in {initial_industry} (top 10 skills)",
    template="simple_white",
    hovermode="closest",
    legend_title_text="Skill",
    margin=dict(l=40, r=200, t=80, b=40),
)

fig.show()



In [203]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px

# ---- 1. Filter to one country (Algeria) ----
country = "Algeria"

df = skill_flow[skill_flow["Country"] == country].copy()
df = df.sort_values(["Industry", "Year", "Skill Rank"])

industries = sorted(df["Industry"].unique())
years = sorted(df["Year"].unique())

# ---- 2. Global color map: same color for a skill across all industries ----
all_skills = sorted(df["Skill"].unique())
base_colors = px.colors.qualitative.Plotly + px.colors.qualitative.D3
color_map = {s: base_colors[i % len(base_colors)] for i, s in enumerate(all_skills)}

# ---- 3. Build one trace per (industry, skill) ----
fig = go.Figure()
trace_industries = []  # to know which trace belongs to which industry

initial_industry = industries[0]  # default shown at start

for ind in industries:
    df_ind = df[df["Industry"] == ind]

    for skill in sorted(df_ind["Skill"].unique()):
        sd = df_ind[df_ind["Skill"] == skill].sort_values("Year")
        if sd.empty:
            continue

        visible_flag = (ind == initial_industry)

        fig.add_trace(
            go.Scatter(
                x=sd["Year"],
                y=sd["Skill Rank"],
                mode="lines+markers",
                name=skill,
                legendgroup=skill,  # same legend entry per skill across industries
                line=dict(
                    color=color_map[skill],
                    width=2,
                    shape="spline"   # smoother line
                ),
                marker=dict(size=8),
                hovertemplate=(
                    f"<b>{skill}</b><br>" +
                    f"Industry: {ind}<br>" +
                    "Year: %{x}<br>" +
                    "Rank: %{y}<extra></extra>"
                ),
                visible=visible_flag
            )
        )
        trace_industries.append(ind)

# ---- 4. Dropdown to filter by industry ----
buttons = []
for ind in industries:
    visible = [ (trace_industries[i] == ind) for i in range(len(trace_industries)) ]

    buttons.append(
        dict(
            label=ind,
            method="update",
            args=[
                {"visible": visible},
                {"title": f"{country} – Skill rank evolution in {ind} (all skills)"}
            ]
        )
    )

fig.update_layout(
    updatemenus=[
        dict(
            buttons=buttons,
            direction="down",
            showactive=True,
            x=0.02,
            xanchor="left",
            y=1.15,
            yanchor="top"
        )
    ]
)

# ---- 5. Axes & style ----
fig.update_yaxes(
    autorange="reversed",   # 1 at the top
    title="Skill rank (1 = top)"
)
fig.update_xaxes(
    title="Year",
    tickmode="linear"
)

fig.update_layout(
    title=f"{country} – Skill rank evolution in {initial_industry} (all skills)",
    template="simple_white",
    hovermode="closest",
    legend_title_text="Skill",
    margin=dict(l=40, r=260, t=80, b=40)
)

fig.show()
